In [1]:
%%capture output
!pip install --upgrade pip
# !pip install --upgrade pandas
!pip install tables   
# necessary for pd.read_hdf()

!pip install ipywidgets
!pip install --upgrade jupyter
!pip install IProgress
!pip install catboost
!pip install shap

In [2]:
import os
import random
import datetime
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.model_selection import KFold, GroupKFold

In [3]:
%matplotlib inline
from tqdm.notebook import tqdm
import gc
import pickle

import torch
import torch.nn as nn
from torch.nn import functional as F
from torch.utils.data import Dataset, DataLoader

device = torch.device("cuda")
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)

## data load

In [4]:
lrz_path = '/dss/dssfs02/lwp-dss-0001/pn36po/pn36po-dss-0001/di93zoj/open-problems-multimodal-3rd-solution/'

model_path_for_now = '/dss/dsshome1/02/di93zoj/valentina/open-problems-multimodal-3rd-solution/'

raw_path =  lrz_path + 'input/raw/'  # '../../../input/raw/'

cite_target_path = lrz_path + 'input/target/cite/'   # '../../../input/target/cite/'
cite_feature_path = lrz_path + 'input/features/cite/'   # '../../../input/features/cite/'
cite_mlp_path = lrz_path + 'model/cite/mlp/'   # '../../../model/cite/mlp/'   # '../../../model/cite/mlp/'
cite_cb_path = lrz_path + 'model/cite/cb/'   # '../../../model/cite/cb/'

multi_target_path = lrz_path + 'input/target/multi/'   # '../../../input/target/multi/'
multi_feature_path = lrz_path + 'input/features/multi/'   # '../../../input/features/multi/'
multi_mlp_path = lrz_path + 'model/multi/mlp/'   # '../../../model/multi/mlp/'
multi_cb_path = lrz_path + 'model/multi/cb/'   # '../../../model/multi/cb/'

index_path = lrz_path + 'input/preprocess/cite/'

output_path = lrz_path + 'output/'   # '../../../output/'

## Cite

In [5]:
# get model name
#mlp_model_path = os.listdir(cite_mlp_path)

In [6]:
mlp_model_name = [
    'corr_add_con_imp',
    'corr_last_v3', 
    'corr_c_add_w2v_v1_mish_flg',
    'corr_c_add_w2v_v1_flg',
    'corr_c_add_84_v1',
    'corr_c_add_120_v1',
    'corr_w2v_cell_flg',
    'corr_best_cell_120',
    'corr_cluster_cell',
    'corr_w2v_128',
    'corr_imp_w2v_128',
    'corr_snorm',
    'corr_best_128',
    'corr_best_64',
    'corr_cluster_128',
    'corr_cluster_64',
    'corr_svd_128',
    'corr_svd_64',
             ]

In [7]:
model_name_list = []

for i in mlp_model_name:
    for num, j in enumerate(os.listdir(cite_mlp_path)):
        if i in j:
            model_name_list.append(j)

len(model_name_list)
model_name_list

['cite_mlp_corr_add_con_imp_flg_donor_val_50',
 'cite_mlp_corr_last_v3_flg_donor_val_55',
 'cite_mlp_corr_c_add_w2v_v1_mish_flg_donor_val_66',
 'cite_mlp_corr_c_add_w2v_v1_flg_donor_val_66',
 'cite_mlp_corr_c_add_84_v1_flg_donor_val_47',
 'cite_mlp_corr_c_add_120_v1_flg_donor_val_63',
 'cite_mlp_corr_w2v_cell_flg_donor_val_51',
 'cite_mlp_corr_best_cell_120_flg_donor_val_51',
 'cite_mlp_corr_cluster_cell_flg_donor_val_64',
 'cite_mlp_corr_w2v_128_flg_donor_val_42',
 'cite_mlp_corr_imp_w2v_128_flg_donor_val_38',
 'cite_mlp_corr_snorm_flg_donor_val_39',
 'cite_mlp_corr_best_128_flg_donor_val_45',
 'cite_mlp_corr_best_64_flg_donor_val_50',
 'cite_mlp_corr_cluster_128_flg_donor_val_51',
 'cite_mlp_corr_cluster_64_flg_donor_val_57',
 'cite_mlp_corr_svd_128_flg_donor_val_30',
 'cite_mlp_corr_svd_64_flg_donor_val_38']

In [8]:
weight = [1, 0.3, 1, 1, 1, 1, 1, 1, 1, 0.8, 0.8, 0.8, 0.8, 0.5, 0.5, 0.5, 1, 1, 2, 2]
weight_sum = np.array(weight).sum()
weight_sum

model_feat_dict = {model_name_list[0]:['X_test_add_con_imp.pickle', 1],
                   model_name_list[1]:['X_test_last_v3.pickle', 0.3],
                   model_name_list[2]:['X_test_c_add_w2v_v1.pickle', 1],
                   model_name_list[3]:['X_test_c_add_w2v_v1.pickle', 1],
                   model_name_list[4]:['X_test_c_add_84_v1.pickle', 1],
                   model_name_list[5]:['X_test_c_add_v1.pickle', 1],
                   
                   model_name_list[6]:['X_test_feature_w2v_cell.pickle', 1],
                   model_name_list[7]:['X_test_best_cell_128_120.pickle', 1],
                   model_name_list[8]:['X_test_cluster_cell_128.pickle', 1],
                   
                   model_name_list[9]:['X_test_feature_w2v.pickle', 0.8],
                   model_name_list[10]:['X_test_feature_imp_w2v.pickle',0.8],
                   model_name_list[11]:['X_test_feature_snorm.pickle', 0.8],
                   model_name_list[12]:['X_test_best_128.pickle', 0.8],
                   model_name_list[13]:['X_test_best_64.pickle', 0.5],
                   model_name_list[14]:['X_test_cluster_128.pickle', 0.5],
                   model_name_list[15]:['X_test_cluster_64.pickle', 0.5],
                   model_name_list[16]:['X_test_svd_128.pickle', 1],
                   model_name_list[17]:['X_test_svd_64.pickle', 1],
                   
                   'best_128':['X_test_best_128.pickle', 2],
                   'best_64':['X_test_best_64.pickle', 2],
                  }

### cite model

In [9]:
def std(x):
    x = np.array(x)
    return (x - x.mean(1).reshape(-1, 1)) / x.std(1).reshape(-1, 1)

In [10]:
class CiteDataset(Dataset):
    
    def __init__(self, feature, target):
        
        self.feature = feature
        self.target = target
        
    def __len__(self):
        return len(self.feature)
    
    def __getitem__(self, index):
                
        d = {
            "X": self.feature[index],
            "y" : self.target[index],
        }
        return d

In [11]:
class CiteDataset_test(Dataset):
    
    def __init__(self, feature):
        self.feature = feature
        
    def __len__(self):
        return len(self.feature)
    
    def __getitem__(self, index):
                
        d = {
            "X": self.feature[index]
        }
        return d

In [12]:
def partial_correlation_score_torch_faster(y_true, y_pred):
    """Compute the correlation between each rows of the y_true and y_pred tensors.
    Compatible with backpropagation.
    """
    y_true_centered = y_true - torch.mean(y_true, dim=1)[:,None]
    y_pred_centered = y_pred - torch.mean(y_pred, dim=1)[:,None]
    cov_tp = torch.sum(y_true_centered*y_pred_centered, dim=1)/(y_true.shape[1]-1)
    var_t = torch.sum(y_true_centered**2, dim=1)/(y_true.shape[1]-1)
    var_p = torch.sum(y_pred_centered**2, dim=1)/(y_true.shape[1]-1)
    return cov_tp/torch.sqrt(var_t*var_p)

def correl_loss(pred, tgt):
    """Loss for directly optimizing the correlation.
    """
    return -torch.mean(partial_correlation_score_torch_faster(tgt, pred))

In [13]:
class CiteModel(nn.Module):
    
    def __init__(self, feature_num):
        super(CiteModel, self).__init__()
        
        self.layer_seq_256 = nn.Sequential(nn.Linear(feature_num, 256),
                                           nn.Linear(256, 128),
                                       nn.LayerNorm(128),
                                       nn.ReLU(),
                                      )
        self.layer_seq_64 = nn.Sequential(nn.Linear(128, 64),
                                       nn.Linear(64, 32),
                                       nn.LayerNorm(32),
                                       nn.ReLU(),
                                      )
        self.layer_seq_8 = nn.Sequential(nn.Linear(32, 16),
                                         nn.Linear(16, 8),
                                       nn.LayerNorm(8),
                                       nn.ReLU(),
                                      )
        
        self.head = nn.Linear(128 + 32 + 8, 140)
                   
    def forward(self, X, y=None):
        
        from_numpy = False
        
      ##
        if isinstance(X, np.ndarray):
            X = torch.from_numpy(X)
            from_numpy = True
        X = X.to(device)  # Move the input to the appropriate device if necessary
        ##
        X_256 = self.layer_seq_256(X)
        X_64 = self.layer_seq_64(X_256)
        X_8 = self.layer_seq_8(X_64)
        
        X = torch.cat([X_256, X_64, X_8], axis = 1)
        out = self.head(X)
        
        if from_numpy:
            out = out.cpu().detach().numpy()
            
        return out

In [14]:
class CiteModel_mish(nn.Module):
    
    def __init__(self, feature_num):
        super(CiteModel_mish, self).__init__()
        
        self.layer_seq_256 = nn.Sequential(nn.Linear(feature_num, 256),
                                           nn.Linear(256, 128),
                                       nn.LayerNorm(128),
                                       nn.Mish(),
                                      )
        self.layer_seq_64 = nn.Sequential(nn.Linear(128, 64),
                                       nn.Linear(64, 32),
                                       nn.LayerNorm(32),
                                       nn.Mish(),
                                      )
        self.layer_seq_8 = nn.Sequential(nn.Linear(32, 16),
                                         nn.Linear(16, 8),
                                       nn.LayerNorm(8),
                                       nn.Mish(),
                                      )
        
        self.head = nn.Linear(128 + 32 + 8, 140)
                   
    def forward(self, X, y=None):
    
        X_256 = self.layer_seq_256(X)
        X_64 = self.layer_seq_64(X_256)
        X_8 = self.layer_seq_8(X_64)
        
        X = torch.cat([X_256, X_64, X_8], axis = 1)
        out = self.head(X)
        
        return out

In [15]:
def train_loop(model, optimizer, loader, epoch):
    
    losses, lrs = [], []
    model.train()
    optimizer.zero_grad()
    #loss_fn = nn.MSELoss()
    
    with tqdm(total=len(loader),unit="batch") as pbar:
        pbar.set_description(f"Epoch{epoch}")
        
        for d in loader:
            X = d['X'].to(device)
            y = d['y'].to(device)
            
            logits = model(X)
            loss = correl_loss(logits, y)
            #loss = torch.sqrt(loss_fn(logits, y))
        
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            
            pbar.set_postfix({"loss":loss.item()})
            pbar.update(1)

    return model

In [16]:
def valid_loop(model, loader, y_val):
    
    model.eval()
    partial_correlation_scores = []
    oof_pred = []
    
    for d in loader:
        with torch.no_grad():
            val_X = d['X'].to(device).float()
            val_y = d['y'].to(device)
            logits = model(val_X)
            oof_pred.append(logits)
    
    #print(torch.cat(oof_pred).shape, torch.cat(oof_pred).detach().cpu().numpy().shape)
    cor = partial_correlation_score_torch_faster(torch.tensor(y_val).to(device), torch.cat(oof_pred))
    cor = cor.mean().item()
    logits = torch.cat(oof_pred).detach().cpu().numpy()
    
    return logits, cor

In [17]:
def test_loop(model, loader):
    
    model.eval()
    predicts=[]

    for d in tqdm(loader):
        with torch.no_grad():
            X = d['X'].to(device)
            logits = model(X)
            predicts.append(logits.detach().cpu().numpy())
            
    return np.concatenate(predicts)

### pred

In [18]:
pred = np.zeros([48203, 140])

for num, i in enumerate(model_feat_dict.keys()):
    
    print(i)
    
    if 'mlp' in i:

        try:
            test_file = model_feat_dict[i][0]
            test_weight = model_feat_dict[i][1]
            X_test = pd.read_pickle(cite_feature_path  + test_file)   
            # print(cite_feature_path  + test_file)
            X_test = np.array(X_test)
            feature_dims = X_test.shape[1]

            test_ds = CiteDataset_test(X_test)
            test_dataloader = DataLoader(test_ds, batch_size=128, pin_memory=True, 
                                         shuffle=False, drop_last=False, num_workers=4)

            if 'mish' in i:
                model = CiteModel_mish(feature_dims)
            else:
                model = CiteModel(feature_dims)

            model = model.to(device)
            model.load_state_dict(torch.load(f'{cite_mlp_path}/{i}'))

            result = test_loop(model, test_dataloader).astype(np.float32)
            result = std(result) * test_weight / weight_sum
            pred += result

            torch.cuda.empty_cache()

        except Exception as e: 
            print(i)
            print(e)             # TODOOOOOOOOOOOOOO
        
    else:
        test_file = model_feat_dict[i][0]
        test_weight = model_feat_dict[i][1]
        X_test = pd.read_pickle(cite_feature_path  + test_file)
        
        cb_pred = np.zeros([48203, 140])
        
        for t in tqdm(range(140)): 
            cb_model_path = [j for j in os.listdir(cite_cb_path) if f'cb_{t}_{i}' in j][0]
            cb = pickle.load(open(cite_cb_path + cb_model_path, 'rb'))
            cb_pred[:,t] = cb.predict(X_test)
            
        cb_pred = cb_pred.astype(np.float32)
        pred += std(cb_pred) * test_weight / weight_sum
        
        #del cb_pred

cite_mlp_corr_add_con_imp_flg_donor_val_50
cite_mlp_corr_add_con_imp_flg_donor_val_50
Attempting to deserialize object on CUDA device 0 but torch.cuda.device_count() is 0. Please use torch.load with map_location to map your storages to an existing device.
cite_mlp_corr_last_v3_flg_donor_val_55
cite_mlp_corr_last_v3_flg_donor_val_55
Attempting to deserialize object on CUDA device 0 but torch.cuda.device_count() is 0. Please use torch.load with map_location to map your storages to an existing device.
cite_mlp_corr_c_add_w2v_v1_mish_flg_donor_val_66
cite_mlp_corr_c_add_w2v_v1_mish_flg_donor_val_66
Attempting to deserialize object on CUDA device 0 but torch.cuda.device_count() is 0. Please use torch.load with map_location to map your storages to an existing device.
cite_mlp_corr_c_add_w2v_v1_flg_donor_val_66
cite_mlp_corr_c_add_w2v_v1_flg_donor_val_66
Attempting to deserialize object on CUDA device 0 but torch.cuda.device_count() is 0. Please use torch.load with map_location to map your st

  0%|          | 0/140 [00:00<?, ?it/s]

TBB Warning: The number of workers is currently limited to 9. The request for 255 workers is ignored. Further requests for more workers will be silently ignored until the limit changes.



best_64


  0%|          | 0/140 [00:00<?, ?it/s]

In [19]:
cite_sub = pd.DataFrame(pred.round(6))
cite_sub

0         1         2         3         4         5         6    \
0     -0.076877 -0.107536 -0.081412  0.235340  0.212383  0.508778  0.714871   
1     -0.070980 -0.105483 -0.078728  0.238921  0.227432  0.494300  0.868887   
2     -0.089150 -0.101540 -0.076435  0.338878  0.290691  0.323657  1.014777   
3     -0.128470 -0.113081 -0.063264  0.226137  0.264680  0.215720 -0.138097   
4     -0.098286 -0.099954 -0.073080  0.293693  0.327439  0.424508  0.117842   
...         ...       ...       ...       ...       ...       ...       ...   
48198 -0.016057 -0.107369 -0.078000  0.223535  0.230541  0.471154  0.740946   
48199 -0.061787 -0.099345 -0.079985  0.165232  0.196600  0.482482  0.507181   
48200 -0.085076 -0.019765 -0.040139  0.082385  0.178649  0.263367 -0.078611   
48201 -0.129128 -0.097133 -0.064378  0.162504  0.062285  0.240771 -0.116835   
48202 -0.128947 -0.098698 -0.057946  0.218069  0.022791  0.350670 -0.102106   

            7         8         9         10        11        12        13   \
0     -0.111080 -0.094659 -0.073315 -0.116281 -0.108862 -0.097573 -0.104481   
1     -0.106807 -0.090079 -0.077481 -0.116207 -0.105719 -0.089185 -0.101150   
2     -0.105268 -0.083472 -0.092418 -0.112782 -0.102729 -0.092453 -0.097368   
3     -0.083314 -0.076588 -0.114464 -0.140753 -0.099502 -0.109232 -0.089628   
4     -0.105193 -0.083176 -0.068864 -0.113596 -0.103659 -0.095560 -0.098380   
...         ...       ...       ...       ...       ...       ...       ...   
48198 -0.114454 -0.088883 -0.078458 -0.118445 -0.109615 -0.099668 -0.103614   
48199 -0.118028 -0.091818 -0.062635 -0.120118 -0.105835 -0.095377 -0.101149   
48200  0.071203 -0.063911 -0.069864 -0.083776 -0.077414 -0.075413 -0.075839   
48201 -0.087210 -0.052549 -0.122759 -0.147196 -0.094668 -0.111958 -0.072857   
48202 -0.103211 -0.043552 -0.122771 -0.151379 -0.090858 -0.109797 -0.072558   

            14        15        16        17        18        19        20   \
0      0.483716 -0.079324  0.426531  0.302832  0.053903 -0.107653 -0.082257   
1      0.476003 -0.084783  0.395964  0.322830  0.022176 -0.101084 -0.087909   
2      0.790603 -0.063658  0.255258  0.259364 -0.007930 -0.099144 -0.079277   
3      0.474046 -0.116054  0.243485 -0.126989 -0.007528 -0.024485 -0.085576   
4      0.289770 -0.070396  0.368481  0.002567  0.077985 -0.103401 -0.072822   
...         ...       ...       ...       ...       ...       ...       ...   
48198  0.533335 -0.093516  0.431017  0.300968  0.044993 -0.107427 -0.092964   
48199  0.428801 -0.083683  0.413566  0.389086  0.066568 -0.108848 -0.103644   
48200 -0.033571 -0.073414  0.257971 -0.079189 -0.061539 -0.076336 -0.070014   
48201  0.228428 -0.128448  0.152343 -0.079240 -0.124319 -0.094852 -0.056010   
48202  0.254119 -0.140788  0.047334 -0.110243 -0.089642 -0.105401  0.020027   

            21        22        23        24        25        26        27   \
0      0.090119 -0.112168 -0.095676  0.687361 -0.113379 -0.115403 -0.108167   
1      0.063508 -0.109683 -0.085107  0.715892 -0.106425 -0.111527 -0.107168   
2      0.090837 -0.107481 -0.086070  0.681157 -0.103144 -0.109113 -0.100578   
3      0.149265 -0.118302 -0.085031  0.411208 -0.119124 -0.130412 -0.142772   
4      0.125669 -0.108211 -0.097858  0.873365 -0.102820 -0.112430 -0.101254   
...         ...       ...       ...       ...       ...       ...       ...   
48198  0.076197 -0.114851 -0.082166  0.715034 -0.115262 -0.116341 -0.106765   
48199  0.079706 -0.113725 -0.058829  0.653562 -0.110858 -0.116593 -0.107356   
48200  0.390727 -0.065538 -0.059764 -0.016561 -0.076601 -0.081644 -0.079352   
48201  0.237674 -0.138501 -0.093899  0.322706 -0.115159 -0.138109 -0.150201   
48202  0.257454 -0.131807 -0.100073  0.455913 -0.115058 -0.134402 -0.150518   

            28        29        30        31        32        33        34   \
0     -0.117696 -0.108534 -0.111692 -0.104854 -0.105364 -0.105601 -0.103499   
1     -0.115465 -0.103104 -0.106192 -0.099530 -0.101643 -0

In [ ]:
#cite_sub.to_csv('../../../../../summary/output/submit/cite_submit.csv')

In [20]:
# model #16: cite_mlp_corr_svd_128_flg_donor_val_30
pred_16 = np.zeros([48203, 140])

i = 'cite_mlp_corr_svd_128_flg_donor_val_30'
        
test_file = model_feat_dict[i][0]
test_weight = model_feat_dict[i][1]
X_test = pd.read_pickle(cite_feature_path  + test_file)
X_test = np.array(X_test)
feature_dims = X_test.shape[1]

test_ds = CiteDataset_test(X_test)
test_dataloader = DataLoader(test_ds, batch_size=128, pin_memory=True, 
                              shuffle=False, drop_last=False, num_workers=4)

if 'mish' in i:
    model = CiteModel_mish(feature_dims)
else:
    model = CiteModel(feature_dims)
    
model = model.to(device)
model.load_state_dict(torch.load(f'{cite_mlp_path}/{i}'))

result = test_loop(model, test_dataloader).astype(np.float32)
pred_16 += result

torch.cuda.empty_cache()
        
pd.DataFrame(pred_16)   # double check train_cite_targets.h5  -> omnipath

RuntimeError: Attempting to deserialize object on CUDA device 0 but torch.cuda.device_count() is 0. Please use torch.load with map_location to map your storages to an existing device.

### - add cell_ids to train and test data
### - SHAP

In [21]:
train_ids = np.load(index_path + "train_cite_raw_inputs_idxcol.npz", allow_pickle=True)
test_ids = np.load(index_path + "test_cite_raw_inputs_idxcol.npz", allow_pickle=True)

train_index = train_ids["index"]
train_column = train_ids["columns"]
test_index = test_ids["index"]
print(len(list(train_index)))
print(len(list(test_index)))
X_train_cell_ids = pd.read_pickle(cite_feature_path  + 'X_svd_128.pickle')   # = X_svd_128 in make-features second to last cell
X_train_cell_ids.index = train_index
X_train_cell_ids

70988
48203


base_svd_0  base_svd_1  base_svd_2  base_svd_3  base_svd_4  \
45006fe3e4c8   85.125969   -5.213882   -9.165653    2.846810   -8.684980   
d02759a80ba2   84.171577   -3.236094  -11.785154    4.179153   -9.126214   
c016c6b0efa5   83.271439   -5.525773   -0.661609    4.323587   10.823631   
ba7f733a4f75   91.433098   -3.291331   -0.577611  -11.340687   -3.523291   
fbcf2443ffb2   93.312256  -11.029425    9.195133   -3.865963    1.862723   
...                  ...         ...         ...         ...         ...   
650ee456f0f3   80.521996   -2.107512   -6.517617    6.813837   -5.033430   
cc506e7707f5   88.921501  -12.732268    7.070011    2.051365    3.950896   
a91f1b55a520   87.540314   -5.718856    5.091103    4.243832   11.409262   
3a9882c98205   89.630875    6.399840    7.432660  -14.750682    1.366882   
c91b6b2ccd3d   84.178833   -3.164330    1.913813    7.093701    7.283193   

              base_svd_5  base_svd_6  base_svd_7  base_svd_8  base_svd_9  \
45006fe3e4c8    1.042275    1.625518    0.619070   -2.840409    0.843441   
d02759a80ba2    4.196675    1.779621   -0.646586    1.247943   -1.225001   
c016c6b0efa5    7.771268   -5.908378   -4.021186    2.341784    2.447490   
ba7f733a4f75    5.469055    6.948833   -1.131284    0.476290    2.398355   
fbcf2443ffb2    1.327440   -2.211365    0.308086   -8.437166    1.691814   
...                  ...         ...         ...         ...         ...   
650ee456f0f3    1.806351    0.527488   -3.493047    1.905602   -1.990217   
cc506e7707f5    4.776496    0.759942   -2.567970    2.431186    4.065137   
a91f1b55a520    4.688626   -4.084728   -4.572702    1.657590    0.820156   
3a9882c98205    3.141237    1.039099    1.786307   -5.499689   -3.747918   
c91b6b2ccd3d    4.032767   -0.593576   -1.978876   -5.816928   -2.345704   

              base_svd_10  base_svd_11  base_svd_12  base_svd_13  base_svd_14  \
45006fe3e4c8     4.115829     0.024965    -1.137678    -2.111087     0.099981   
d02759a80ba2     4.100103     3.394336     0.073237    -1.664542    -1.158479   
c016c6b0efa5     2.764741    -0.793546     0.339175    -1.861371    -0.397006   
ba7f733a4f75    -0.937833     2.288733     1.341390    -1.259106     0.586084   
fbcf2443ffb2    -4.531765    -1.196248     1.671790    -2.604029     0.095138   
...                   ...          ...          ...          ...          ...   
650ee456f0f3    -1.776384    -1.505758    -3.821366    -2.135085    -0.165477   
cc506e7707f5    -2.780904    -1.426755    -0.259897    -1.230719    -0.750336   
a91f1b55a520     1.047736     2.144724     1.173932     1.229822    -0.821481   
3a9882c98205    -0.316761    -4.189414     3.514624    -2.080882     4.804155   
c91b6b2ccd3d     2.191808     1.821924    -4.687260     0.087143     0.659438   

              base_svd_15  base_svd_16  base_svd_17  base_svd_18  base_svd_19  \
45006fe3e4c8     1.337295    -0.596183    -0.751670     1.757503     1.105504   
d02759a80ba2    -3.064280    -0.290697    -0.023197     0.734850    -0.166198   
c016c6b0efa5    -3.334067     0.469813     0.909500     1.036141    -2.195434   
ba7f733a4f75    -1.854470     2.050018    -3.391635     2.778138     2.048289   
fbcf2443ffb2    -2.018014    -0.372212     0.158817     0.730702    -2.444231   
...                   ...          ...          ...          ...          ...   
650ee456f0f3     1.015598    -1.086126     1.687963    -2.726144    -1.984358   
cc506e7707f5     2.807658     0.220193    -1.989150    -2.811765    -0.031830   
a91f1b55a520    -1.769283     2.717549     3.942862    -0.775065    -0.527137   
3a9882c98205    -0.064423     0.640573     5.758480    -1.524391     0.458360   
c91b6b2ccd3d     1.799906     0.476140     1.383227    -0.749666     2.008985   

              base_svd_20  base_svd_21  base_svd_22  base_svd_23  base_svd_24  \
45006fe3e4c8     0.548275     1.499717     1.038158    -0.272647    -1.365031   
d02759a80ba2    -0.808781     0.506946     0.695540    -0.009503     1.300577   

In [25]:
# cell type from metadata
X_test_cell_ids = pd.read_pickle(cite_feature_path  + test_file)
X_test_cell_ids.index = test_index
X_test_cell_ids

base_svd_0  base_svd_1  base_svd_2  base_svd_3  base_svd_4  \
83d6659a6a32   94.056297   -7.824483    0.390148  -11.240480    1.049213   
d98594f13d2e   92.367874   -4.847517    0.514445   -8.376771   -1.919603   
5f93d8ffc72f   90.292252    0.146880   -0.271159  -10.908630   -3.214201   
7dfa2699d351   93.805962  -12.445390   10.555358   -0.710891    4.603803   
6d2533edd0e0   88.557716  -11.090774   -5.711870    2.695317  -10.597410   
...                  ...         ...         ...         ...         ...   
a9b4d99f1f50   85.366356    1.080519   -8.010132    0.796445   -3.396977   
0e2c1d0782af   81.205399    6.503594  -10.942855    2.147213    1.046774   
a3cbc5aa0ec3   80.439636    7.672957   15.710591   15.690635    8.388031   
75b350243add   84.337151   -3.197404    1.886770    5.541795   13.938139   
ad5a949989b2   87.705643  -10.010480    5.631869    3.797515    8.066127   

              base_svd_5  base_svd_6  base_svd_7  base_svd_8  base_svd_9  \
83d6659a6a32   -6.360567   -0.291657   -0.807333    1.523107    4.391570   
d98594f13d2e   -4.256521   -1.352172    5.257206    1.822807    2.321193   
5f93d8ffc72f    5.237493    3.355039    3.375244    2.553044    0.776845   
7dfa2699d351   -2.805171    1.068830    1.833984   -4.608570   -0.201459   
6d2533edd0e0    1.775790    1.812456    3.326061   -5.383945    0.696400   
...                  ...         ...         ...         ...         ...   
a9b4d99f1f50    1.601400    3.458448   -1.217016    0.786072    4.255503   
0e2c1d0782af   -0.758410    1.365951   -1.823899    1.040893    4.043109   
a3cbc5aa0ec3   -5.819407   22.253601    1.320871    0.245843   -0.062292   
75b350243add    6.305854   -4.405701   -3.572052    2.690609    0.877849   
ad5a949989b2    9.830094   -6.498420    2.366302    4.272543    3.918396   

              base_svd_10  base_svd_11  base_svd_12  base_svd_13  base_svd_14  \
83d6659a6a32     1.058334     1.107465     2.794737     0.232357     0.485993   
d98594f13d2e     2.636189     2.633024     0.982998     0.518114     0.128080   
5f93d8ffc72f     0.540434     3.613944     1.005818     0.078405     2.192658   
7dfa2699d351    -3.962924    -0.005088    -1.098507    -1.379581     0.761541   
6d2533edd0e0     1.563926    -0.765326    -0.380334    -0.970265    -0.079944   
...                   ...          ...          ...          ...          ...   
a9b4d99f1f50    -2.755232     0.385691     2.922162     1.191900    -3.223046   
0e2c1d0782af    -0.935470     0.734516    -1.798569     2.394704    -2.455899   
a3cbc5aa0ec3     6.345723     0.137742     0.052358    -0.312850    -1.177019   
75b350243add     3.526787     0.154360     1.378285     0.823426    -1.125885   
ad5a949989b2     3.832386     0.275236     1.521225     1.476691     0.951005   

              base_svd_15  base_svd_16  base_svd_17  base_svd_18  base_svd_19  \
83d6659a6a32     0.610800     1.087533    -3.675157    -2.152177     0.258529   
d98594f13d2e     0.306104     1.269342    -2.080164    -2.541140     0.760104   
5f93d8ffc72f    -0.775795     2.759478    -2.709326    -0.784265     1.249367   
7dfa2699d351    -3.148588     2.913516     0.101658     0.022856     1.432993   
6d2533edd0e0     1.173417     1.223524    -2.820121     0.673842    -1.156821   
...                   ...          ...          ...          ...          ...   
a9b4d99f1f50     0.136868     0.361752     0.188772    -3.447983    -1.681520   
0e2c1d0782af     0.074219    -1.513982     0.663842    -4.000921    -0.806638   
a3cbc5aa0ec3     1.313636     1.003704     0.869457    -3.321661     0.135167   
75b350243add    -1.530648     2.033235     1.787222    -0.625443    -0.946741   
ad5a949989b2     0.124911     0.361213    -1.355333    -2.168039    -0.255948   

              base_svd_20  base_svd_21  base_svd_22  base_svd_23  base_svd_24  \
83d6659a6a32    -0.241675    -0.281301    -0.892517     3.144524    -1.095826   
d98594f13d2e    -0.550402    -2.429527     0.044688     0.752230     0.119079   

In [27]:
metadata = pd.read_csv('/dss/dssfs02/lwp-dss-0001/pn36po/pn36po-dss-0001/di93zoj/neurips_competition_data/' + 'metadata.csv')
metadata.head()

cell_id  day  donor cell_type technology
0  c2150f55becb    2  27678       HSC    citeseq
1  65b7edf8a4da    2  27678       HSC    citeseq
2  c1b26cb1057b    2  27678      EryP    citeseq
3  917168fa6f83    2  27678      NeuP    citeseq
4  2b29feeca86d    2  27678      EryP    citeseq

In [28]:
X_test_cell_ids = X_test_cell_ids.reset_index().rename(columns = {'index': 'cell_id'})
X_test_cell_ids = X_test_cell_ids.merge(metadata[['cell_id', 'cell_type']], on = 'cell_id', how = 'left')

In [29]:
X_test_cell_ids['cell_type'].value_counts()

HSC     9451
MasP    9064
EryP    8788
NeuP    7719
MkP     4844
MoP     1215
BP       106
Name: cell_type, dtype: int64

In [30]:
X_test_cell_ids

cell_id  base_svd_0  base_svd_1  base_svd_2  base_svd_3  \
0      83d6659a6a32   94.056297   -7.824483    0.390148  -11.240480   
1      d98594f13d2e   92.367874   -4.847517    0.514445   -8.376771   
2      5f93d8ffc72f   90.292252    0.146880   -0.271159  -10.908630   
3      7dfa2699d351   93.805962  -12.445390   10.555358   -0.710891   
4      6d2533edd0e0   88.557716  -11.090774   -5.711870    2.695317   
...             ...         ...         ...         ...         ...   
48198  a9b4d99f1f50   85.366356    1.080519   -8.010132    0.796445   
48199  0e2c1d0782af   81.205399    6.503594  -10.942855    2.147213   
48200  a3cbc5aa0ec3   80.439636    7.672957   15.710591   15.690635   
48201  75b350243add   84.337151   -3.197404    1.886770    5.541795   
48202  ad5a949989b2   87.705643  -10.010480    5.631869    3.797515   

       base_svd_4  base_svd_5  base_svd_6  base_svd_7  base_svd_8  base_svd_9  \
0        1.049213   -6.360567   -0.291657   -0.807333    1.523107    4.391570   
1       -1.919603   -4.256521   -1.352172    5.257206    1.822807    2.321193   
2       -3.214201    5.237493    3.355039    3.375244    2.553044    0.776845   
3        4.603803   -2.805171    1.068830    1.833984   -4.608570   -0.201459   
4      -10.597410    1.775790    1.812456    3.326061   -5.383945    0.696400   
...           ...         ...         ...         ...         ...         ...   
48198   -3.396977    1.601400    3.458448   -1.217016    0.786072    4.255503   
48199    1.046774   -0.758410    1.365951   -1.823899    1.040893    4.043109   
48200    8.388031   -5.819407   22.253601    1.320871    0.245843   -0.062292   
48201   13.938139    6.305854   -4.405701   -3.572052    2.690609    0.877849   
48202    8.066127    9.830094   -6.498420    2.366302    4.272543    3.918396   

       base_svd_10  base_svd_11  base_svd_12  base_svd_13  base_svd_14  \
0         1.058334     1.107465     2.794737     0.232357     0.485993   
1         2.636189     2.633024     0.982998     0.518114     0.128080   
2         0.540434     3.613944     1.005818     0.078405     2.192658   
3        -3.962924    -0.005088    -1.098507    -1.379581     0.761541   
4         1.563926    -0.765326    -0.380334    -0.970265    -0.079944   
...            ...          ...          ...          ...          ...   
48198    -2.755232     0.385691     2.922162     1.191900    -3.223046   
48199    -0.935470     0.734516    -1.798569     2.394704    -2.455899   
48200     6.345723     0.137742     0.052358    -0.312850    -1.177019   
48201     3.526787     0.154360     1.378285     0.823426    -1.125885   
48202     3.832386     0.275236     1.521225     1.476691     0.951005   

       base_svd_15  base_svd_16  base_svd_17  base_svd_18  base_svd_19  \
0         0.610800     1.087533    -3.675157    -2.152177     0.258529   
1         0.306104     1.269342    -2.080164    -2.541140     0.760104   
2        -0.775795     2.759478    -2.709326    -0.784265     1.249367   
3        -3.148588     2.913516     0.101658     0.022856     1.432993   
4         1.173417     1.223524    -2.820121     0.673842    -1.156821   
...            ...          ...          ...          ...          ...   
48198     0.136868     0.361752     0.188772    -3.447983    -1.681520   
48199     0.074219    -1.513982     0.663842    -4.000921    -0.806638   
48200     1.313636     1.003704     0.869457    -3.321661     0.135167   
48201    -1.530648     2.033235     1.787222    -0.625443    -0.946741   
48202     0.124911     0.361213    -1.355333    -2.168039    -0.255948   

       base_svd_20  base_svd_21  base_svd_22  base_svd_23  base_svd_24  \
0        -0.241675    -0.281301    -0.892517     3.144524    -1.095826   
1        -0.550402    -2.429527     0.044688     0.752230     0.119079   
2         0.050844    -2.158159     0.776920     0.989583    -1.557484   
3        -2.331087    -1.915733    -1.166527     2.186154     1.076372   
4        -0.484202     0.746177     0.

In [ ]:
samples_per_cell_type = 5

grouped = X_test_cell_ids.groupby('cell_type')

X_test_shap = pd.DataFrame()

# Iterate over each group (cell_type)
for cell_type, group in grouped:
    sampled_rows = group.sample(n=samples_per_cell_type, replace=False)
    X_test_shap = X_test_shap.append(sampled_rows)

X_test_shap = X_test_shap.reset_index(drop=True)
X_test_shap

/tmp/ipykernel_3841981/137142177.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  X_test_shap = X_test_shap.append(sampled_rows)
/tmp/ipykernel_3841981/137142177.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  X_test_shap = X_test_shap.append(sampled_rows)
/tmp/ipykernel_3841981/137142177.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  X_test_shap = X_test_shap.append(sampled_rows)
/tmp/ipykernel_3841981/137142177.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  X_test_shap = X_test_shap.append(sampled_rows)
/tmp/ipykernel_3841981/137142177.py:10: FutureWarning: The frame.append method is deprecated and will be removed

In [32]:
# rename imp_ columns to gene ids:
gene_ids = ['ENSG00000075340_ADD2', 'ENSG00000233968_AL157895.1',
        'ENSG00000029534_ANK1', 'ENSG00000135046_ANXA1',
        'ENSG00000130208_APOC1', 'ENSG00000047648_ARHGAP6',
        'ENSG00000101200_AVP', 'ENSG00000166710_B2M',
        'ENSG00000130303_BST2', 'ENSG00000172247_C1QTNF4',
        'ENSG00000170458_CD14', 'ENSG00000134061_CD180',
        'ENSG00000177455_CD19', 'ENSG00000116824_CD2',
        'ENSG00000206531_CD200R1L', 'ENSG00000012124_CD22',
        'ENSG00000272398_CD24', 'ENSG00000139193_CD27',
        'ENSG00000105383_CD33', 'ENSG00000174059_CD34',
        'ENSG00000135218_CD36', 'ENSG00000004468_CD38',
        'ENSG00000010610_CD4', 'ENSG00000026508_CD44',
        'ENSG00000117091_CD48', 'ENSG00000169442_CD52',
        'ENSG00000135404_CD63', 'ENSG00000173762_CD7',
        'ENSG00000137101_CD72', 'ENSG00000019582_CD74',
        'ENSG00000105369_CD79A', 'ENSG00000085117_CD82',
        'ENSG00000114013_CD86', 'ENSG00000010278_CD9',
        'ENSG00000002586_CD99', 'ENSG00000166091_CMTM5',
        'ENSG00000119865_CNRIP1', 'ENSG00000100368_CSF2RB',
        'ENSG00000100448_CTSG', 'ENSG00000051523_CYBA',
        'ENSG00000116675_DNAJC6', 'ENSG00000142227_EMP3',
        'ENSG00000143226_FCGR2A', 'ENSG00000167996_FTH1',
        'ENSG00000139278_GLIPR1', 'ENSG00000130755_GMFG',
        'ENSG00000169567_HINT1', 'ENSG00000206503_HLA-A',
        'ENSG00000234745_HLA-B', 'ENSG00000204287_HLA-DRA',
        'ENSG00000196126_HLA-DRB1', 'ENSG00000204592_HLA-E',
        'ENSG00000171476_HOPX', 'ENSG00000076662_ICAM3',
        'ENSG00000163565_IFI16', 'ENSG00000142089_IFITM3',
        'ENSG00000160593_JAML', 'ENSG00000055118_KCNH2',
        'ENSG00000105610_KLF1', 'ENSG00000139187_KLRG1',
        'ENSG00000133816_MICAL2', 'ENSG00000198938_MT-CO3',
        'ENSG00000107130_NCS1', 'ENSG00000090470_PDCD7',
        'ENSG00000143627_PKLR', 'ENSG00000109099_PMP22',
        'ENSG00000117450_PRDX1', 'ENSG00000112077_RHAG',
        'ENSG00000108107_RPL28', 'ENSG00000198918_RPL39',
        'ENSG00000145425_RPS3A', 'ENSG00000198034_RPS4X',
        'ENSG00000196154_S100A4', 'ENSG00000197956_S100A6',
        'ENSG00000188404_SELL', 'ENSG00000124570_SERPINB6',
        'ENSG00000235169_SMIM1', 'ENSG00000095932_SMIM24',
        'ENSG00000137642_SORL1', 'ENSG00000128040_SPINK2',
        'ENSG00000072274_TFRC', 'ENSG00000205542_TMSB4X',
        'ENSG00000133112_TPT1', 'ENSG00000026025_VIM']

In [33]:
new_columns = []
for col in X_test_shap.columns:
    if col.startswith('imp_'):
        col = gene_ids[int(col.split('_')[1])]
    new_columns.append(col)
X_test_shap.columns = new_columns
X_test_shap

cell_id  base_svd_0  base_svd_1  base_svd_2  base_svd_3  base_svd_4  \
0   2acc5555e459   83.767593   11.069773    7.322483   14.772043   -8.992854   
1   90a09b6b576b   82.944504   12.334619    9.663526   10.058416   -5.097158   
2   23acde7482e4   91.928398   -7.556545    8.990211    0.176704   -4.897999   
3   dbd0d1a8b759   92.568657   -5.764327   11.112267   -2.596874   -2.861043   
4   3e98ed3715bc   91.954796   -3.752177   10.814301   -2.263846    1.222814   
5   353efbaf98b7   87.948647  -11.737404    4.927299    6.167234    4.031952   
6   cc9f6e656071   84.883316   -9.767824    4.090904    6.809038    8.950108   
7   372c769fe5ee   86.242256   -0.282864    3.311511   12.950950    3.445004   
8   1cd4496c00b2   83.205162   -7.361337    2.464623    4.933367    9.424631   
9   9e7845d94b96   87.956642   -6.229804    4.691976    6.585415   -5.727653   
10  8c02c52ad31c   87.079712   -3.473468   -4.560095    0.012823   -3.916837   
11  eac84a23f5b3   86.975655   -1.341050   -8.204206   -1.027663   -0.836000   
12  6cb9bbe7119e   88.387100   -3.914439   -0.177864   -1.979723   -1.646309   
13  8485a04856c4   88.018173   -4.210809   -5.869287   -1.955749   -4.050073   
14  9d3a6210b968   81.253151    1.453624  -11.512630    6.107981   -3.208295   
15  530ff70241b5   91.681000   -1.562518   10.176538   -8.161019   -3.238353   
16  c10a258c57f0   71.340950   24.515520   -1.116771    0.415561    6.799320   
17  ded2aee29f30   86.821274    6.220806    3.998892   -2.020773    0.538719   
18  52d48fa878e8   73.850639   22.907415   13.556305   10.216696  -14.166386   
19  3fc0d4156f19   86.872566   12.074393   13.514866   -4.999821   -7.493195   
20  df52eba31284   88.751160   -3.400106   15.176248    7.998569    8.767797   
21  d935ee9142ad   89.804016  -11.169793    8.231398    4.474523   -1.034250   
22  f72793ee1a3d   85.861237   -2.473394   15.296535   10.118040    5.450414   
23  442eb35acc8e   87.868439    1.896169   19.088650    9.982913   10.343547   
24  c0a38b1a3b74   84.784012    2.024732   12.884568   17.653536    5.680970   
25  137a1058d76f   87.455185    4.768830   11.471695    0.481879   -4.383562   
26  44d88362966d   86.638313    5.634543    8.003178    3.282592   -6.713991   
27  16907413f837   81.721954   15.437891   -1.504253    5.686324    1.817084   
28  50a12f99d11f   91.670860   -2.093915    5.128953   -1.839857   -6.194622   
29  a5c23dd337d3   80.240288   16.479424    6.230208    6.864201   -2.515670   
30  5e77ee67f272   67.845078   21.220278   -8.136497   -7.877395   10.392011   
31  e9e4f34e498c   89.321831    1.447672    0.070006  -11.378035   -0.049714   
32  c0721e44abe0   82.449638   14.521996   -1.629200  -12.370481    8.794700   
33  4377cd7a645d   81.002556    8.161515   -2.186184  -10.797945    0.432538   
34  cd3a179cc5dc   73.245476   20.761068   -6.532765   -3.140975    5.018486   

    base_svd_5  base_svd_6  base_svd_7  base_svd_8  base_svd_9  base_svd_10  \
0     1.291030   -1.648193   -3.445352   -2.359793    0.622657    -2.593606   
1    -2.116637   -3.882306   -5.366705   -0.351370    2.021426    -2.644504   
2     2.066076   -0.475175   -0.226412   -6.252208    0.314048    -4.404939   
3     0.062450   -0.741830   -3.001451   -5.899223    1.798374    -3.946074   
4    -1.652760   -0.114158   -7.866723    1.229529    0.040917    -7.064013   
5     9.218928    0.252105   -1.976181   -3.457729    3.602390     2.023234   
6     9.268728   -8.844852    6.922394    1.906960    4.674007     2.551399   
7     3.257172    2.924091   -3.437458   -5.062040    2.186059    -8.754500   
8     8.201796   -4.476068   -2.395453    3.655853    4.650548     0.550416   
9     5.875120   -1.338523    0.310257   -5.817238   -1.400475    -0.703710   
10   -4.255982   -1.541080    2.950803    4.595518    2.459343     0.652890   
11    0.394283    1.015819   -2.893029    1.636590    1.492131     1.854923   
12    2.112806   -0.652657   -2.279124   -4.754938   -3.131627     2.951764   
13    1.042940    1.83

In [34]:
import shap

# X_train for model #16: 'X_svd_128.pickle'
X_train = pd.read_pickle(cite_feature_path  + 'X_svd_128.pickle')
X_train = np.array(X_train)
print('X_train: ', X_train.shape)
print('X_test: ', X_test.shape)

explainer = shap.KernelExplainer(model, shap.sample(X_train, 1000))
explainer

Using 1000 background data samples could cause slower run times. Consider using shap.sample(data, K) or shap.kmeans(data, K) to summarize the background as K samples.


X_train:  (70988, 212)
X_test:  (48203, 212)


In [35]:
xtest = X_test_shap#.drop(['cell_id', 'cell_type'], axis=1)

In [ ]:
# features: genes and svd -> omnipath: genes
# model: mostly relying on genes or svd? -> later

In [ ]:
# don't need to run again: np.load('shap_values.npy', allow_pickle=True)
# %timeit
# shap_values = explainer.shap_values(xtest, nsamples=300)  #500? 
# print(len(shap_values)) # -> 140 genes
# print(len(shap_values[0])) # -> number of samples in xtest
# print(shap_values[0].shape)

# np.save('shap_values.npy', np.array(shap_values, dtype=object), allow_pickle=True)

In [36]:
shap_values = np.load('shap_values.npy', allow_pickle=True).astype(float)

In [37]:
shap_values

array([[[-1.25789386e-03, -2.89969019e-02,  1.96794373e-01, ...,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
        [ 0.00000000e+00,  3.27279295e-02,  3.18742828e-01, ...,
          0.00000000e+00, -3.81334645e-04,  0.00000000e+00],
        [ 0.00000000e+00,  1.56157456e-02,  2.11980305e-01, ...,
          0.00000000e+00,  0.00000000e+00,  2.03371406e-02],
        ...,
        [ 0.00000000e+00,  1.42697456e-01,  0.00000000e+00, ...,
          0.00000000e+00,  0.00000000e+00,  2.23412310e-03],
        [-2.86447129e-03,  2.53864986e-02,  0.00000000e+00, ...,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
        [ 0.00000000e+00,  1.30203116e-01,  2.73106251e-03, ...,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00]],

       [[-9.13210696e-03,  0.00000000e+00,  2.95975910e-02, ...,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00],
        [ 0.00000000e+00,  2.18054098e-03,  7.20618668e-02, ...,
          0.00000000e+00,  0.00000000e

### plot shap values per cell type similar to shap.summary_plot(shap_values[0], xtest)

In [ ]:
# shap_values that are plotted in beeswarm below
# [0,:,2] == base_svd_2; [0,:,1] == base_svd_1 etc
second_element = shap_values[0, :, 9]
print(second_element)
print(min(second_element))
max(second_element)

In [ ]:
# print top 10 features plotted in beeswarm plot below
shap_sum = np.abs(shap_values[0]).sum(axis=0)
top_features_indices = np.argsort(shap_sum)[::-1][:10]  # Get the indices of the top 10 features
top_feature_names = xtest.drop(['cell_id', 'cell_type'], axis=1).columns[top_features_indices]
top_feature_names

In [ ]:
shap_cell_types = pd.DataFrame({'SHAP svd_2': shap_values[0, :, 2], 
                                'SHAP svd_9': shap_values[0, :, 9], 
                                'SHAP svd_1': shap_values[0, :, 1], 
                                'SHAP svd_16': shap_values[0, :, 16], 
                                'SHAP svd_11': shap_values[0, :, 11], 
                                'SHAP svd_7': shap_values[0, :, 7], 
                                'SHAP svd_4': shap_values[0, :, 4], 
                                'SHAP svd_6': shap_values[0, :, 6], 
                                'SHAP CD36': shap_values[0, :, 150], # xtest.columns.get_loc('ENSG00000135218_CD36')+1
                                'SHAP svd_21': shap_values[0, :, 21], 
                                'Cell Type': xtest['cell_type']})
shap_cell_types

In [ ]:
# Assign different colors to each class
colors = {'BP': 'red', 'EryP': 'blue', 'HSC': 'green', 'MasP': 'orange', 'MkP': 'purple', 'MoP': 'yellow', 'NeuP': 'pink'}

## legend ##
legend_fig, legend_ax = plt.subplots(figsize=(2, 2))

for class_label, color in colors.items():
    legend_ax.scatter([], [], color=color, label=f'Cell type {class_label}')

legend_ax.legend(loc='center', bbox_to_anchor=(0.5, 1.2), ncol=len(colors), frameon=False)
legend_ax.axis('off')
## legend ##


# plot shap values:
fig, ax = plt.subplots(figsize=(8, 10))

x_limit = (-0.2, 0.5)

# Remove y-axis ticks and labels
ax.yaxis.set_visible(False)

# Iterate over the columns in shap_cell_types to create subplots
for i, column in enumerate(shap_cell_types.columns[:-1], start=1):

    ax = fig.add_subplot(len(shap_cell_types.columns)-1, 1, i)

    # Set the x-axis limits and label
    ax.set_xlim(x_limit)
    ax.set_xlabel(column)

    ax.yaxis.set_visible(False)

    # Plot the dots for the current column
    for index, row in shap_cell_types.iterrows():
        shap_value = row[column]
        class_label = row['Cell Type']
        color = colors[class_label]
        ax.plot(shap_value, 0, marker='o', color=color)

        
fig.tight_layout(rect=[0, 0.1, 1, 1]) 
legend_fig.subplots_adjust(top=0.1, bottom=0.05)

plt.show()

In [ ]:
shap.initjs()
shap.summary_plot(shap_values[0], xtest.drop(['cell_id', 'cell_type'], axis=1), feature_names=xtest.drop(['cell_id', 'cell_type'], axis=1).columns)#color=xtest['cell_type']) 

# goal: get this plot as SHAP / features instead of SHAP / SVD components + features


In [ ]:
shap.initjs()
shap.summary_plot(list(shap_values), plot_type = 'bar', feature_names = xtest.drop(['cell_id', 'cell_type'], axis=1).columns)
# 140 classes = each regression output

In [ ]:
shap.initjs()
shap.force_plot(explainer.expected_value[3], shap_values[3], feature_names = xtest.drop(['cell_id', 'cell_type'], axis=1).columns)

### svd contributions:

In [41]:
svd_comp_norm = np.loadtxt('/dss/dsshome1/02/di93zoj/valentina/open-problems-multimodal-3rd-solution/code/2.preprocess_to_feature/cite/svd_comp_norm.txt', delimiter=',')
pd.DataFrame(svd_comp_norm)

0         1             2             3             4      \
0    2.639231e-06  0.000006  8.334996e-07  5.828498e-06  2.757570e-08   
1    2.210494e-04  0.000259  3.542308e-04  5.002551e-04 -4.445526e-07   
2   -1.809794e-05 -0.000001  3.091744e-06 -6.833360e-05  1.926849e-07   
3   -1.261245e-05 -0.000043 -1.826978e-05 -6.340233e-07 -1.083960e-07   
4    1.866322e-05 -0.000028  4.857562e-06  7.331298e-05  8.726915e-07   
5    4.506983e-05  0.000070  3.077376e-05  1.205591e-04 -3.135513e-07   
6   -4.218275e-05 -0.000028  1.913090e-04  6.590385e-05 -8.933609e-07   
7    1.064613e-04  0.000267  1.316198e-04  6.470450e-04  1.296479e-05   
8    5.436529e-05  0.000738 -3.131564e-04  1.541981e-04 -2.304106e-05   
9   -1.530041e-05  0.000005  5.171535e-04 -1.986017e-04 -1.232986e-06   
10   7.600606e-07 -0.000014  1.344043e-04  1.049197e-04 -7.783138e-07   
11   3.873259e-05  0.000151  4.035431e-04 -2.226786e-05  4.639964e-06   
12   8.713726e-06 -0.000003 -4.275802e-05 -1.971396e-05 -4.941238e-07   
13  -2.846578e-05 -0.000011  7.780871e-05  3.199106e-04 -6.731819e-06   
14   1.984658e-05  0.000165  6.615551e-04  1.304688e-04 -7.120664e-06   
15   1.777616e-05  0.000136  7.493119e-05  4.368735e-05  3.673612e-06   
16   3.881814e-05  0.000208 -4.385633e-05  2.287749e-04 -8.576018e-06   
17   7.567060e-06 -0.000213 -4.410144e-03  9.890533e-04 -4.100242e-05   
18   1.071626e-06 -0.000065 -8.971484e-06 -8.001163e-05  6.014086e-06   
19  -2.860269e-04  0.000706  6.720136e-04 -1.152031e-03 -1.982567e-05   
20  -5.198477e-06 -0.000651 -8.308486e-04 -3.813874e-04  9.203550e-06   
21   1.720900e-04  0.000399 -6.771822e-04  5.657123e-04 -6.335367e-07   
22   2.446261e-04 -0.000661  8.365403e-04 -1.160566e-03 -2.718989e-05   
23  -1.996536e-04 -0.000882  5.225797e-04  1.313114e-03 -1.124968e-05   
24   3.597293e-05 -0.000015 -1.346985e-05  1.027365e-04 -1.294113e-06   
25   5.376680e-05  0.000353 -1.012158e-03 -3.446337e-03  2.462551e-05   
26   2.882832e-04  0.000329 -7.936843e-04 -1.137226e-03 -4.398718e-06   
27  -3.688878e-06 -0.000071  1.427657e-04  4.578981e-04  4.739499e-06   
28   3.117527e-05 -0.000167 -1.088876e-03  8.025829e-05 -8.632772e-06   
29  -4.082438e-04  0.000469 -5.474071e-04 -2.841509e-04 -4.348257e-07   
30   7.552408e-05  0.000069  1.634458e-04  1.417547e-04 -8.261444e-06   
31   1.121376e-03  0.001264  2.899160e-03 -3.069043e-04 -2.388874e-06   
32  -6.770726e-05  0.000165  9.756357e-05 -3.552889e-04  6.001875e-07   
33   9.473236e-05 -0.002387  5.717970e-03  8.164378e-03 -6.239591e-05   
34   8.680289e-05  0.000137  7.736558e-04  4.708983e-04  2.953622e-05   
35  -1.265974e-04  0.000247 -5.854431e-04 -3.197264e-04  2.944493e-05   
36   7.197419e-05 -0.000066  9.046419e-05  2.949845e-05  4.936455e-07   
37  -6.365163e-05 -0.000078  4.768181e-04  2.568117e-04  9.665325e-07   
38   3.396894e-05 -0.000738  2.024290e-03 -8.880977e-04 -1.025665e-05   
39   2.417970e-05  0.000097  8.658431e-06 -3.205733e-05  2.461498e-06   
40  -3.032340e-05 -0.000057  7.445801e-06  2.862267e-04  3.715536e-06   
41  -1.349161e-04 -0.000085  5.736885e-04 -7.757180e-05 -1.211610e-06   
42   1.976254e-05 -0.000161 -4.938822e-04  4.168452e-04  4.319060e-06   
43  -5.524596e-05  0.000100  5.490614e-04 -1.989546e-04 -3.667349e-06   
44   6.640792e-04  0.000316  2.149119e-03 -1.028622e-03  6.248181e-05   
45   6.654386e-05  0.000162  7.119613e-05  2.096224e-04 -1.210518e-05   
46   1.256810e-04  0.000366  7.692830e-04  3.153055e-04 -2.523692e-05   
47  -9.167763e-05  0.000150 -3.397762e-04 -6.156388e-04 -1.483039e-05   
48  -6.699134e-05 -0.000044  4.650250e-05 -4.989313e-04  2.704992e-06   
49  -1.913718e-04  0.000497 -1.359685e-03 -1.773176e-03 -1.611218e-05   
50   5.174652e-05 -0.000188 -5.757256e-04 -1.267754e-05 -5.999727e-06   
51  -1.826241e-05  0.000135  3.520784e-04  1.679333e-04 -4.924111e-07   
52  -2.702002e-04 -0.001032 -4.398305e-04  1.081941e-03  9.451037e-05   
53  -2.608043e-04  0.000237 -9.734188e-04  8.055048e-04  1.970178e-05 

In [44]:
pd.DataFrame(shap_values[0])

0         1         2         3         4         5         6    \
0  -0.001258 -0.028997  0.196794  0.000000  0.000000  0.000000  0.028894   
1   0.000000  0.032728  0.318743  0.008943  0.010122 -0.013775  0.012584   
2   0.000000  0.015616  0.211980  0.000000  0.028795  0.000000  0.032422   
3   0.000000  0.201583 -0.113936  0.018501 -0.011257 -0.053279  0.015758   
4   0.000000  0.000000  0.278029  0.004335  0.067960  0.015729  0.000000   
5   0.010892 -0.025995  0.038889 -0.031127 -0.100119  0.038524  0.087306   
6   0.000000 -0.076878  0.076079 -0.029781 -0.104058  0.042729  0.034026   
7   0.000000 -0.056570  0.037351  0.000000 -0.083353  0.018128  0.120404   
8   0.000000 -0.008724  0.108095  0.000000 -0.013239 -0.001041  0.026050   
9   0.000000 -0.136478  0.034053 -0.014514  0.038112  0.000000  0.000000   
10  0.000000  0.005560  0.000000  0.000000  0.000000 -0.035118  0.000000   
11  0.000000  0.025896 -0.129070  0.004660  0.000000  0.032878 -0.015049   
12  0.000000  0.111780 -0.143454  0.000000 -0.027275 -0.023493  0.000000   
13 -0.013352  0.015622 -0.098178  0.018604  0.000000  0.037807  0.000000   
14  0.004957  0.158861 -0.037755  0.000000  0.000000  0.000000 -0.014096   
15  0.021272  0.121977  0.133340  0.002707  0.118211  0.000000  0.052773   
16  0.000000  0.140096  0.279844  0.000000  0.036053  0.031050  0.029567   
17  0.000000  0.090167  0.162629  0.001924  0.031102  0.039539  0.000000   
18  0.008373  0.214488  0.159798  0.031309  0.041189  0.042131  0.000000   
19  0.000000  0.041621  0.129075  0.000000  0.000000  0.025145  0.000000   
20 -0.005784 -0.028292  0.054178 -0.041215  0.000000  0.000000  0.027671   
21  0.000000  0.000000  0.074635  0.001701 -0.009295  0.000000 -0.045717   
22  0.000000  0.000000  0.206197  0.000000 -0.047110  0.008214 -0.020756   
23  0.014699  0.000000  0.124425 -0.020528 -0.076140  0.004031 -0.036037   
24  0.000000 -0.039812  0.120620  0.000000 -0.038412 -0.004926 -0.034946   
25  0.014738  0.121977  0.171060  0.000000  0.030365  0.000000  0.000000   
26  0.000938  0.033990  0.163902  0.000000  0.012872 -0.034624  0.027243   
27  0.000000  0.197232  0.107796  0.000000  0.000000  0.015979  0.000000   
28  0.000000  0.117747  0.052556  0.000000  0.043220  0.037495 -0.044736   
29  0.000000  0.129013  0.026004  0.000000  0.000000 -0.000603 -0.040047   
30  0.000000  0.076657  0.119819  0.000000  0.000000  0.007731 -0.058082   
31  0.000000  0.088878  0.004402 -0.014370  0.000000  0.028936 -0.048079   
32  0.000000  0.142697  0.000000  0.000000  0.000000  0.036709 -0.006021   
33 -0.002864  0.025386  0.000000  0.000000  0.007589  0.000000 -0.024845   
34  0.000000  0.130203  0.002731  0.000000  0.000000  0.041481 -0.017715   

         7         8         9         10        11        12        13   \
0   0.000963 -0.007535 -0.028404 -0.026043  0.054919  0.000000  0.000000   
1   0.000000  0.000000  0.023219 -0.019991 -0.008505 -0.010018  0.031958   
2   0.084197  0.000000  0.000000 -0.053274  0.017783  0.000000  0.000000   
3   0.000000  0.000000  0.156891  0.000000 -0.022656  0.000000  0.000000   
4   0.000000  0.000000 -0.048922  0.000000  0.000000  0.000000  0.009522   
5   0.000000 -0.010681  0.029975  0.054102  0.000000  0.000000  0.000000   
6  -0.014523 -0.014748  0.046473  0.000000  0.000000  0.000000  0.000000   
7  -0.036330  0.000000  0.056855  0.019155 -0.035249  0.000000 -0.016883   
8  -0.026164 -0.003137 -0.044065  0.000000  0.000000  0.000000  0.000000   
9   0.026593  0.000000 -0.029177  0.000000  0.000000 -0.017876  0.000000   
10 -0.023624  0.000000 -0.007139 -0.009168 -0.030042  0.000000  0.000000   
11  0.000000  0.000000  0.027303 -0.011300  0.000000  0.000000  0.000000   
12  0.006982  0.000000  0.000000  0.000000  0.000000  0.000000  0.033691   
13 -0.025192  0.006219  0.000000  0.000000  0.018029  0.000000  0.013838   
14  0.021942  0.000000  0.000000 -0.025339  0.078809  0.000000 -0.032497   
15  0.082165  0.028452  0.102579  0.027183 -0.073862  0.

In [73]:
# multiply SHAP(svd_n)*contribution of gene A to component n -> sum
# each dot in summary_plot is attribution for one cell -> loop over all cells

# 212 features: 128 svd and 84 genes
# cells: 35
# predicted "classes": 140

# contribution of gene A to component n: svd_comp_norm
# SHAP(svd_n) for the 128 svd (=first 128 columns)

all_attr_A = []

for cell in range(len(xtest)):
    attr_gene_A = 0    # (first column)
    for svd in range(128):
        attr_gene_A += shap_values[0][cell][svd] * svd_comp_norm[svd][0]   # this is for one cell (first row)
    #print(attr_gene_A)
    all_attr_A.append(attr_gene_A)

all_attr_A

[4.732174071345578e-06,
 0.00013540043121407233,
 3.751044086756874e-05,
 -0.00015474951456323266,
 3.6368247871949225e-05,
 -0.00013936397999118194,
 -1.121661645588132e-05,
 -0.00011541837556790292,
 -3.231336478127482e-05,
 -5.898688226278096e-05,
 3.7638477526196314e-05,
 8.142455406314581e-05,
 5.4491269509745335e-05,
 6.021113276889802e-05,
 4.2899450547565304e-05,
 8.719014279345223e-05,
 1.4714259912949594e-05,
 7.351842567763794e-06,
 0.0001601442877346193,
 -1.7209951866457397e-05,
 1.8894056345382088e-05,
 0.00012115565569800993,
 8.372940727422912e-05,
 -4.6940026320579296e-05,
 -0.0001853808821023433,
 7.57573159351505e-05,
 5.900691900147709e-06,
 8.066594198527494e-06,
 3.58723267678572e-06,
 -1.4301878464135375e-05,
 -2.7527681558947567e-05,
 2.4704108055360264e-06,
 5.163130193882175e-06,
 -1.3190676303964357e-06,
 3.9912405109513975e-05]

In [68]:
attr_gene_A = 0    # (first column)
for svd in range(128):
    attr_gene_A += shap_values[0][0][svd] * svd_comp_norm[svd][0] 
attr_gene_A

4.732174071345578e-06

In [74]:
attr_gene_B = 0    # (second column)
for i in range(128):
    attr_gene_B += shap_values[0][0][i] * svd_comp_norm[i][1]   # this is for one cell (first row)

attr_gene_B

-3.473335300311415e-05

In [48]:
# base_svd_2 important feature
svd_comp_norm[2]         # => contribution x_2 = -0.00001809 * geneA - 0.00000149 * geneB + 0.0000030917 * geneC + ... + 0.0001264 geneX + 0.00026577 geneY + 0.000175 geneZ

array([-1.80979350e-05, -1.49000311e-06,  3.09174447e-06, ...,
        1.26464845e-04,  2.65770446e-04,  1.75062174e-04])

In [ ]:
xtest['base_svd_9']

In [ ]:
stop

## Multi

In [ ]:
mlp_model_name = [
    'multi_mlp_all_con_16',
    'multi_mlp_all_con_32', 
    'multi_mlp_all_binary_16',
    'multi_mlp_all_last_cluster',
    'multi_mlp_all_lsi_w2v_col_128_flg',
    'multi_mlp_all_lsi_w2v_128_flg',
    'multi_mlp_all_lsi_128_flg',
    'multi_mlp_all_lsi_w2v_col_64_flg',
    'multi_mlp_all_lsi_w2v_64_flg',
    'multi_mlp_all_lsi_64_flg',
    'multi_mlp_all_okapi_128_flg',
    'multi_mlp_all_okapi_64_flg',
    'multi_mlp_all_colmean_64_flg',
    'multi_mlp_corr_con_16_flg',
    'multi_mlp_corr_con_32_flg',
    'multi_mlp_corr_binary_16',
    'multi_mlp_corr_lsi_add_lc_svd_flg',
    
    'multi_mlp_corr_lsi_w2v_col_128_flg',
    'multi_mlp_corr_lsi_w2v_col_64_flg',
    'multi_mlp_corr_lsi_w2v_128_flg',
    'multi_mlp_corr_lsi_w2v_64_flg',
    
    'multi_mlp_corr_lsi_128_flg',
    'multi_mlp_corr_lsi_64_flg',
    
    'multi_mlp_corr_colmean_64_flg',
    'multi_mlp_corr_okapi_w2v_64_flg',
    'multi_mlp_corr_okapi_64_flg',
    
             ]

In [ ]:
model_name_list = []

for i in mlp_model_name:
    for num, j in enumerate(os.listdir(multi_mlp_path)):
        if i in j:
            model_name_list.append(j)

print(len(model_name_list))
model_name_list

In [ ]:
weight = [2.5, 2.5, 2.5, 1.2, 1.2, 1.2, 1, 
          1.5, 1.5, 2.5, 0.5, 0.5, 0.5, 
          2.5, 2.5, 1.8, 0.8, 1, 0.8, 1 ,0.8, 1, 0.3, 
          0.3, 0.3, 0.3, 0.2, 0.2, 0.2]
weight_sum = np.array(weight).sum()
weight_sum

model_feat_dict = {model_name_list[0]:['multi_test_con_16.pickle', 2.5],
                   model_name_list[1]:['multi_test_con_32.pickle', 2.5],
                   model_name_list[2]:['multi_test_binary_16.pickle', 2.5],
                   
                   model_name_list[3]:['multi_test_okapi_64_last_cluster.pickle', 1.2],
                   model_name_list[4]:['multi_test_lsi_w2v_col_128.pickle', 1.2],
                   model_name_list[5]:['multi_test_lsi_w2v_128.pickle', 1.2],
                   model_name_list[6]:['multi_test_okapi_lsi_128.pickle', 1],
                   
                   model_name_list[7]:['multi_test_lsi_w2v_col_64.pickle', 1.5],
                   model_name_list[8]:['multi_test_lsi_w2v_64.pickle', 1.5],
                   model_name_list[9]:['multi_test_okapi_lsi_64.pickle', 2.5],
                   
                   model_name_list[10]:['multi_test_okapi_feature_128.pickle', 0.5],
                   model_name_list[11]:['multi_test_okapi_feature_64.pickle', 0.5],
                   model_name_list[12]:['multi_test_okapi_w2v_col_64.pickle', 0.5],
                   
                   model_name_list[13]:['multi_test_con_16.pickle', 2.5],
                   model_name_list[14]:['multi_test_con_32.pickle', 2.5],
                   model_name_list[15]:['multi_test_binary_16.pickle', 1.8],
                   model_name_list[16]:['multi_test_lc_addsvd_64.pickle', 0.8],
                   
                   model_name_list[17]:['multi_test_lsi_w2v_col_128.pickle', 1],
                   model_name_list[18]:['multi_test_lsi_w2v_col_64.pickle', 0.8],
                   model_name_list[19]:['multi_test_lsi_w2v_128.pickle', 1],
                   model_name_list[20]:['multi_test_lsi_w2v_64.pickle', 0.8],
                   model_name_list[21]:['multi_test_okapi_lsi_128.pickle', 1],
                   model_name_list[22]:['multi_test_okapi_lsi_64.pickle', 0.3],
                   
                   model_name_list[23]:['multi_test_okapi_w2v_col_64.pickle', 0.3],
                   model_name_list[24]:['multi_test_okapi_w2v_64.pickle', 0.3],
                   model_name_list[25]:['multi_test_okapi_feature_64.pickle', 0.3],
                   
                   'lsi_128':['multi_test_okapi_lsi_128.pickle', 0.2],
                   'lsi_64':['multi_test_okapi_lsi_64.pickle', 0.2],
                   'lsi_w2v_col_64':['multi_test_lsi_w2v_col_64.pickle', 0.2],
                  }


### multi model

In [ ]:
class MultiDataset(Dataset):
    
    def __init__(self, feature, target):
        
        self.feature = feature
        self.target = target
        
    def __len__(self):
        return len(self.feature)
    
    def __getitem__(self, index):
                
        d = {
            "X": self.feature[index],
            "y" : self.target[index],
        }
        return d

In [ ]:
class MultiDataset_test(Dataset):
    
    def __init__(self, feature):
        self.feature = feature
        
    def __len__(self):
        return len(self.feature)
    
    def __getitem__(self, index):
                
        d = {
            "X": self.feature[index]
        }
        return d

In [ ]:
def partial_correlation_score_torch_faster(y_true, y_pred):
    """Compute the correlation between each rows of the y_true and y_pred tensors.
    Compatible with backpropagation.
    """
    y_true_centered = y_true - torch.mean(y_true, dim=1)[:,None]
    y_pred_centered = y_pred - torch.mean(y_pred, dim=1)[:,None]
    cov_tp = torch.sum(y_true_centered*y_pred_centered, dim=1)/(y_true.shape[1]-1)
    var_t = torch.sum(y_true_centered**2, dim=1)/(y_true.shape[1]-1)
    var_p = torch.sum(y_pred_centered**2, dim=1)/(y_true.shape[1]-1)
    return cov_tp/torch.sqrt(var_t*var_p)

def correl_loss(pred, tgt):
    """Loss for directly optimizing the correlation.
    """
    return -torch.mean(partial_correlation_score_torch_faster(tgt, pred))


def correlation_score(y_true, y_pred):
    """Scores the predictions according to the competition rules. 
    
    It is assumed that the predictions are not constant.
    
    Returns the average of each sample's Pearson correlation coefficient"""
    if type(y_true) == pd.DataFrame: y_true = y_true.values
    if type(y_pred) == pd.DataFrame: y_pred = y_pred.values
    if y_true.shape != y_pred.shape: raise ValueError("Shapes are different.")
    corrsum = 0
    for i in range(len(y_true)):
        corrsum += np.corrcoef(y_true[i], y_pred[i])[1, 0]
    return corrsum / len(y_true)

In [ ]:
class MultiModel(nn.Module):
    
    def __init__(self, feature_num):
        super(MultiModel, self).__init__()
        
        self.layer_seq_128 = nn.Sequential(nn.Linear(feature_num, 128),
                                           nn.LayerNorm(128),
                                           nn.ReLU(),
                                      )
        
        self.layer_seq_64 = nn.Sequential(nn.Linear(128, 64),
                                           nn.LayerNorm(64),
                                           nn.ReLU(),
                                      )
        
        self.layer_seq_32 = nn.Sequential(nn.Linear(64, 32),
                                   nn.LayerNorm(32),
                                   nn.ReLU(),
                              )
        
        self.layer_seq_8 = nn.Sequential(nn.Linear(32, 8),
                                         nn.LayerNorm(8),
                                         nn.ReLU(),
                                      )
        
        self.head = nn.Linear(128 + 64 + 32 + 8, target_num)
                   
    def forward(self, X, y=None):
        
        X_128 = self.layer_seq_128(X)
        X_64 = self.layer_seq_64(X_128)
        X_32 = self.layer_seq_32(X_64)
        X_8 = self.layer_seq_8(X_32)
        X = torch.cat([X_128, X_64, X_32, X_8], axis = 1)
        out = self.head(X)
        
        return out

In [ ]:
def train_loop(model, optimizer, loader, epoch):
    
    losses, lrs = [], []
    model.train()
    optimizer.zero_grad()
    loss_fn = nn.MSELoss()
    
    with tqdm(total=len(loader),unit="batch") as pbar:
        pbar.set_description(f"Epoch{epoch}")
        
        for d in loader:
            X = d['X'].to(device).float()
            y = d['y'].to(device)
            
            logits = model(X)
            #loss = correl_loss(logits, y)
            loss = torch.sqrt(loss_fn(logits, y))
        
            optimizer.zero_grad()
            loss.backward()
            optimizer.step()
            
            pbar.set_postfix({"loss":loss.item()})
            pbar.update(1)

    return model

In [ ]:
def valid_loop(model, loader, y_val):
    
    model.eval()
    partial_correlation_scores = []
    oof_pred = []
    loss_fn = nn.MSELoss()
    
    for d in loader:
        with torch.no_grad():
            val_X = d['X'].to(device).float()
            val_y = d['y'].to(device)
            logits = model(val_X)
            #oof_pred.append(logits.detach().cpu().numpy())
            oof_pred.append(logits)
    
    y_val = torch.tensor(y_val).to(device)
    logits = torch.cat(oof_pred)
    #print(logits.shape, y_val.shape)
    loss = torch.sqrt(loss_fn(logits, y_val))
    logits = logits.detach().cpu().numpy()
    
    return logits, loss

In [ ]:
def test_loop(model, loader):
    
    model.eval()
    predicts=[]

    for d in tqdm(loader):
        with torch.no_grad():
            X = d['X'].to(device).float()
            logits = model(X)
            predicts.append(logits.detach().cpu().numpy())
            
    return np.concatenate(predicts)

In [ ]:
pred = np.zeros([55935, 23418])
svd = pickle.load(open(multi_target_path + 'multi_all_target_128.pkl', 'rb'))

for num, i in enumerate(model_feat_dict.keys()):
    
    print(i)
    
    if 'mlp' in i:
        
        test_file = model_feat_dict[i][0]
        test_weight = model_feat_dict[i][1]
        X_test = pd.read_pickle(multi_feature_path  + test_file)    
        X_test = np.array(X_test)
        feature_dims = X_test.shape[1]

        test_ds = MultiDataset_test(X_test)
        test_dataloader = DataLoader(test_ds, batch_size=128, pin_memory=True, 
                                     shuffle=False, drop_last=False, num_workers=4)
        
        if 'all' in i:
            target_num = 23418
        else:
            target_num = 128
        
        model = MultiModel(feature_dims)    
        model = model.to(device)
        model.load_state_dict(torch.load(f'{multi_mlp_path}/{i}'))
        
        result = test_loop(model, test_dataloader).astype(np.float32)
        
        if 'all' not in i:
            result = result@svd.components_
                
        result = result * test_weight / weight_sum
        pred += result

        torch.cuda.empty_cache()
        
    else:
        test_file = model_feat_dict[i][0]
        test_weight = model_feat_dict[i][1]
        X_test = pd.read_pickle(multi_feature_path  + test_file)
        
        cb_pred = np.zeros([55935, 128])
        
        for t in tqdm(range(128)): 
            cb_model_path = [j for j in os.listdir(multi_cb_path) if f'cb_{t}_{i}' in j][0]
            cb = pickle.load(open(multi_cb_path + cb_model_path, 'rb'))
            cb_pred[:,t] = cb.predict(X_test)
            
        cb_pred = cb_pred.astype(np.float32)
        cb_pred = cb_pred@svd.components_
        pred += cb_pred * test_weight / weight_sum
        
        #del cb_pred

In [ ]:
multi_sub = pd.DataFrame(pred.round(6)).astype(np.float32)

In [ ]:
del pred
gc.collect()

## Postprocess

In [ ]:
preprocess_path = '../../../../summary/input/preprocess/'

#### first: fix cite output

In [ ]:
test_sub_ids = np.load(preprocess_path + "cite/test_cite_inputs_idxcol.npz", allow_pickle=True)
test_sub_ids = test_sub_ids["index"]
test_raw_ids = np.load(preprocess_path + "cite/test_cite_raw_inputs_idxcol.npz", allow_pickle=True)
test_raw_ids = test_raw_ids["index"]

In [ ]:
test_cite_df = pd.DataFrame(test_sub_ids, columns = ['cell_id'])
cite_sub['cell_id'] = test_raw_ids
test_cite_df = test_cite_df.merge(cite_sub, on = 'cell_id', how = 'left')
test_cite_df.fillna(0, inplace = True)
test_cite_df.drop(['cell_id'], axis = 1, inplace = True)

cite_sub = test_cite_df.copy()

### preprocess

In [ ]:
sub = pd.read_csv(raw_path + "sample_submission.csv")  
eval_ids = pd.read_csv(raw_path + "evaluation_ids.csv") 

cite_cols = pd.read_csv(preprocess_path + "cite/cite_test_cols.csv") 
cite_index = pd.read_csv(preprocess_path + "cite/cite_test_indexs.csv") 
cite_index.columns = ['cell_id']

multi_cols = pd.read_csv(preprocess_path + "multi/multi_test_cols.csv") 
multi_index = pd.read_csv(preprocess_path + "multi/multi_test_indexs.csv") 
multi_index.columns = ['cell_id']

submission = pd.Series(name='target',index=pd.MultiIndex.from_frame(eval_ids), dtype=np.float32)

### multi

In [ ]:
multi_sub = np.array(multi_sub)

In [ ]:
cell_dict = dict((k,v) for v,k in enumerate(np.array(multi_index['cell_id'])))
assert len(cell_dict)  == len(multi_index['cell_id'])

gene_dict = dict((k,v) for v,k in enumerate(np.array(multi_cols['gene_id']))) 
assert len(gene_dict)  == len(multi_cols['gene_id'])

eval_ids_cell_num = eval_ids.cell_id.apply(lambda x:cell_dict.get(x, -1))
eval_ids_gene_num = eval_ids.gene_id.apply(lambda x:gene_dict.get(x, -1))

valid_multi_rows = (eval_ids_gene_num !=-1) & (eval_ids_cell_num!=-1)
submission.iloc[valid_multi_rows] = multi_sub[eval_ids_cell_num[valid_multi_rows].to_numpy(),
                                                 eval_ids_gene_num[valid_multi_rows].to_numpy()]

### cite

In [ ]:
cite_sub = np.array(cite_sub)

In [ ]:
cell_dict = dict((k,v) for v,k in enumerate(np.array(cite_index['cell_id'])))
assert len(cell_dict)  == len(cite_index['cell_id'])

gene_dict = dict((k,v) for v,k in enumerate(np.array(cite_cols['gene_id']))) 
assert len(gene_dict)  == len(cite_cols['gene_id'])

eval_ids_cell_num = eval_ids.cell_id.apply(lambda x:cell_dict.get(x, -1))
eval_ids_gene_num = eval_ids.gene_id.apply(lambda x:gene_dict.get(x, -1))

valid_multi_rows = (eval_ids_gene_num !=-1) & (eval_ids_cell_num!=-1)

In [ ]:
submission.iloc[valid_multi_rows] = cite_sub[eval_ids_cell_num[valid_multi_rows].to_numpy(),
                                                 eval_ids_gene_num[valid_multi_rows].to_numpy()]

### make submission

In [ ]:
submission = submission.round(6)
submission = pd.DataFrame(submission, columns = ['target'])
submission = submission.reset_index()

In [ ]:
submission[['row_id', 'target']].to_csv(output_path + 'submission.csv', index = False)

In [ ]:
#!kaggle competitions submit -c open-problems-multimodal -f $sub_name_csv -m $message